In [1]:
import pandas as pd
import folium
import numpy as np

In [2]:
#import data
customer_data = pd.DataFrame(pd.read_excel("LaptopSalesLL.xlsx"))

data cleaning

In [3]:
customer_data['Store Latitude'].replace('', np.nan, inplace=True)
customer_data['Store Longitude'].replace('', np.nan, inplace=True)
customer_data['Customer Latitude'].replace('FAILED', np.nan, inplace=True)
customer_data['Customer Longitude'].replace('FAILED', np.nan, inplace=True)
customer_data.dropna(axis=0, subset=["Store Latitude","Store Longitude","Customer Latitude","Customer Longitude"], inplace=True)

In [4]:
stores = customer_data.groupby("Store Postcode").first()

In [5]:
customer_data.isnull().sum()

Date                          0
Configuration                 0
Customer Postcode             0
Store Postcode                0
Retail Price              13415
Screen Size (Inches)          0
Battery Life (Hours)          0
RAM (GB)                      0
Processor Speeds (GHz)        0
Integrated Wireless?          0
HD Size (GB)                  0
Bundled Applications?         0
customer X                    0
customer Y                    0
store X                       0
store Y                       0
Customer Latitude             0
Customer Longitude            0
Store Latitude                0
Store Longitude               0
dtype: int64

In [6]:
stores_locations = stores.loc[:,["Store Latitude", "Store Longitude"]]
sell_counts =  customer_data.groupby("Store Postcode").count()
sell_counts = sell_counts.iloc[:,[0]]
sell_counts.columns= ["sell count"]
stores_df = sell_counts.join(stores_locations)
stores_df.head()

sell count  Store Latitude  Store Longitude
Store Postcode                                             
CR7 8LE               7832       51.398191        -0.093631
E2 0RY               30682       51.529346        -0.045410
E7 8NW                3793       51.541776         0.037959
KT2 5AU               4333       51.418947        -0.305625
N17 6QA               4738       51.593016        -0.070008

In [7]:
customers = customer_data.groupby("Customer Postcode").first()
customers_locations = customers.loc[:,["Customer Latitude", "Customer Longitude"]]
buying_counts =  customer_data.groupby("Customer Postcode").count()
buying_counts = buying_counts.iloc[:,[0]]
buying_counts.columns= ["buying count"]
customers_df = buying_counts.join(customers_locations)
customers_df.head()

buying count Customer Latitude Customer Longitude
Customer Postcode                                                   
BR3 1AG                     335         51.407001          -0.027712
BR3 3LA                     338         51.406189          -0.026496
BR3 4DF                     353         51.398795          -0.045144
CR0 1NA                     354         51.371064          -0.100562
CR0 1NF                     330         51.368895          -0.099891

#### create map base

In [8]:
folium_map = folium.Map(location=[51.5, -0.14],
                        zoom_start=10.5,
                        tiles="CartoDB dark_matter")

folium.CircleMarker(location=[51.5, -0.14],fill=True).add_to(folium_map)
folium_map

In [9]:
for index, row in stores_df.iterrows():
    popup_text = "Total Sales: {}"
    popup_text = popup_text.format(int(row["sell count"]))
    
        
    folium.CircleMarker(location=(row["Store Latitude"],
                                  row["Store Longitude"]),
                         radius=5,
                         color="#E37222",
                         popup=popup_text,
                         fill=True).add_to(folium_map)
folium_map

In [10]:
for index, row in customers_df.iterrows():
   
    popup_text = "Total Purchase: {}"
    popup_text = popup_text.format(int(row["buying count"]))
        
    folium.CircleMarker(location=(float(row["Customer Latitude"]),
                                  float(row["Customer Longitude"])),
                         radius=1,
                         color="#0A8A9F",
                         popup=popup_text,
                         fill=True).add_to(folium_map)
folium_map


In [11]:
customers_stores = customer_data.drop_duplicates(['Customer Postcode', 'Store Postcode'])
customers_stores.head()

Date  Configuration Customer Postcode Store Postcode  \
0 2008-01-01 00:01:19            163          EC4V 5BH        SE1 2BN   
1 2008-01-01 00:02:52            320           SW4 0JL       SW12 9HD   
2 2008-01-01 00:04:18             23          EC3V 1LR         E2 0RY   
3 2008-01-01 00:04:40            169          SW1P 3AU        SE1 2BN   
4 2008-01-01 00:06:04            365          EC4V 4EG       SW1V 4QQ   

   Retail Price  Screen Size (Inches)  Battery Life (Hours)  RAM (GB)  \
0         455.0                    15                     5         1   
1         545.0                    15                     6         1   
2         515.0                    15                     4         1   
3         395.0                    15                     5         1   
4         585.0                    15                     6         2   

   Processor Speeds (GHz) Integrated Wireless?  HD Size (GB)  \
0                     2.0                  Yes            80   
1                     2.0                   No           300   
2                     2.0                  Yes           300   
3                     2.0                   No            40   
4                     2.0                   No           120   

  Bundled Applications?  customer X  customer Y   store X   store Y  \
0                   Yes      532041      180995  534057.0  179682.0   
1                    No      529240      175537  528739.0  173080.0   
2                   Yes      533095      181047  535652.0  182961.0   
3                   Yes      529902      179641  534057.0  179682.0   
4                   Yes      531684      180948  528924.0  178440.0   

  Customer Latitude Customer Longitude  Store Latitude  Store Longitude  
0         51.512579          -0.098731       51.500186        -0.070057  
1         51.464129          -0.140912       51.442082        -0.149046  
2         51.512699          -0.083435       51.529346        -0.045410  
3         51.500787          -0.129897       51.500186        -0.070057  
4          51.51212          -0.103737       51.490255        -0.144474

In [12]:
store_list = ["CR7 8LE","SE8 3JD","SW12 9HD","SW18 1NN","W4 3PH","W10 6HQ","SW1V 4QQ","SW1P 3AU",
             "SE1 2BN","NW5 2QH","N3 1DH","N17 6QA","KT2 5AU","E7 8NW","E2 0RY"]

#### Create the connect line as well as customer highlights

The default map connect all lines, you can select specfic store using the drop down icon on the top right corner. The highlighted customers will turns from blue to yellow.

In [13]:
from folium import FeatureGroup, LayerControl
for store in store_list:
    data = customers_stores.loc[customers_stores['Store Postcode'] == store]
    lablel = folium.FeatureGroup(name = store)
    for index, row in data.iterrows():
        folium.PolyLine(locations=[[float(row["Customer Latitude"]),float(row["Customer Longitude"])],
                               [row["Store Latitude"],row["Store Longitude"]]], weight=0.25).add_to(lablel)
        folium.CircleMarker(location=(float(row["Customer Latitude"]),
                                  float(row["Customer Longitude"])),
                         radius=1,
                         color="yellow").add_to(lablel)
    lablel.add_to(folium_map)

LayerControl().add_to(folium_map)
folium_map

In [14]:
folium_map.save('storemap_version_1.html')

### Version 2 

In [15]:
data =customer_data.drop_duplicates(subset=['Customer Latitude','Customer Longitude','Store Latitude','Store Longitude']).copy()

In [16]:
data.dropna(inplace = True)

In [17]:
data.shape

(2499, 20)

#### Create map base

In [18]:
import folium
storemap = folium.Map(location=[51.5, -0.14],
                        zoom_start=10.5,
                        tiles="CartoDB dark_matter")

folium.CircleMarker(location=[51.5, -0.14],fill=True).add_to(storemap)
storemap

In [19]:
data['Customer Latitude'] = pd.to_numeric(data['Customer Latitude'])

In [20]:
data['Customer Longitude'] = pd.to_numeric(data['Customer Longitude'])

In [21]:
data = data.loc[:,['Customer Latitude','Customer Longitude','Store Latitude','Store Longitude']]

create the map base

In [22]:
location = data.iloc[:,[2,3]].drop_duplicates()

In [23]:
for x in data.dropna().values:
    folium.Circle(location = x[0:2],radius =1,color ="#0A8A9F").add_to(storemap) 

In [24]:
n =1
for y in location.values:
    folium.Marker(location = y,icon=folium.Icon(color='pink',icon='cloud'), \
                  popup = 'store{}'.format(n)).add_to(storemap)
    n += 1

In [25]:
storemap

In [26]:
# group customers by store
from folium import FeatureGroup
n = 1
for eachstore in location.values.tolist():
    feature_group=FeatureGroup(name = '{}{}'.format('store',n),show=True)
    store=[]
    store_customer = data[data.loc[:,'Store Latitude'] == eachstore[0]]
    
    folium.Marker(location = eachstore ,icon=folium.Icon(color='pink',icon='cloud'), \
                  popup = 'store{}'.format(n)).add_to(feature_group)
    n += 1
    for y in store_customer.iloc[:,[0,1]].dropna().values.tolist():
        storeline=[]
        storeline.append(eachstore) 
        storeline.append(y)
        store.append(storeline)
    folium.PolyLine(store,opacity=0).add_to(feature_group)
    feature_group.add_to(storemap)

In [27]:
#take a look at customers for same store
store_customer

Customer Latitude  Customer Longitude  Store Latitude  Store Longitude
194           51.582736           -0.011740       51.593016        -0.070008
229           51.593016           -0.070008       51.593016        -0.070008
287           51.558569           -0.098848       51.593016        -0.070008
298           51.594481           -0.130527       51.593016        -0.070008
332           51.555545           -0.082154       51.593016        -0.070008
390           51.563452           -0.142664       51.593016        -0.070008
462           51.559513           -0.098289       51.593016        -0.070008
651           51.590568           -0.154898       51.593016        -0.070008
693           51.570310           -0.150437       51.593016        -0.070008
713           51.596749           -0.111577       51.593016        -0.070008
857           51.559386           -0.119415       51.593016        -0.070008
873           51.590195           -0.146020       51.593016        -0.070008
984           51.553522           -0.098208       51.593016        -0.070008
1024          51.600827           -0.194725       51.593016        -0.070008
1103          51.553509           -0.122485       51.593016        -0.070008
1112          51.546069           -0.055496       51.593016        -0.070008
1190          51.555522            0.012131       51.593016        -0.070008
1273          51.562276           -0.079144       51.593016        -0.070008
1288          51.565269           -0.105047       51.593016        -0.070008
1298          51.564126           -0.104979       51.593016        -0.070008
1358          51.556105            0.000645       51.593016        -0.070008
1383          51.545907           -0.056051       51.593016        -0.070008
1481          51.556577           -0.116978       51.593016        -0.070008
1565          51.554121           -0.122532       51.593016        -0.070008
1832          51.554665            0.045055       51.593016        -0.070008
1893          51.574651           -0.011169       51.593016        -0.070008
1918          51.590830           -0.156114       51.593016        -0.070008
1989          51.558561           -0.143844       51.593016        -0.070008
2066          51.606715            0.001685       51.593016        -0.070008
2411          51.587147           -0.164390       51.593016        -0.070008
3119          51.575622            0.067860       51.593016        -0.070008
3439          51.583511           -0.010782       51.593016        -0.070008
4004          51.552254           -0.125566       51.593016        -0.070008
4222          51.550757           -0.113497       51.593016        -0.070008
4341          51.564209           -0.121323       51.593016        -0.070008
5887          51.576298            0.011951       51.593016        -0.070008
6695          51.549193           -0.090729       51.593016        -0.070008
6960          51.620250           -0.106759       51.593016        -0.070008
8466          51.629908           -0.196446       51.593016        -0.070008

In [28]:
storemap.save('storemap_version_2.html')

In [29]:
# Create lines connect customers and stores
#click once to show the lines, click again to remove the lines
import re
import fileinput

with open("storemap_version_2.html") as inf:
       txt = inf.read()

polylines = re.findall(r'\bpoly_line_\w+', txt)
polylines = sorted(set(polylines),key=polylines.index)

groups = re.findall(r'\bfeature_group_\w+', txt)
groups = sorted(set(groups),key=groups.index)

count_list =['count_{}'.format(i) for i in range(15)]

for i in range(len(polylines)):
    pattern = "                    .addTo({});\n".format(groups[i])
    variable = "var {} =1;\n".format(count_list[i])
    pattern2 = groups[i] + ".on('click',function(e)"+ '''{
    var layer = e.target;'''+ \
    '{}={}+1'.format(count_list[i],count_list[i],count_list[i])+ \
    '\nif({}%2==0)'.format(count_list[i])+'''{
    layer.setStyle({
        opacity: 1,
        weight: 0.68
    });}
    else{
    layer.setStyle({
        opacity: 0,
        weight: 1
    });
    }       
});\n\n'''


    with open("storemap_version_2.html") as inf:
       txt = inf.read()
    for linenum,line in enumerate( fileinput.FileInput("storemap_version_2.html",inplace=1) ):    
        if pattern in line:
           print(line.rstrip())
           print(variable)
           print(pattern2)
           
        else:
           print(line.rstrip())
with open("scriptofmap.txt", "w") as text_file:
    text_file.write(txt)
       
    

#### please find the storemap.html file in the folder to access the map